<a href="https://colab.research.google.com/github/sipocz/CabPrice/blob/B20210531/CabPrice.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [96]:
!wget https://github.com/sipocz/CabPrice/raw/B20210507/TRAIN.csv

--2021-05-31 20:19:40--  https://github.com/sipocz/CabPrice/raw/B20210507/TRAIN.csv
Resolving github.com (github.com)... 140.82.113.3
Connecting to github.com (github.com)|140.82.113.3|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://raw.githubusercontent.com/sipocz/CabPrice/B20210507/TRAIN.csv [following]
--2021-05-31 20:19:40--  https://raw.githubusercontent.com/sipocz/CabPrice/B20210507/TRAIN.csv
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 7524003 (7.2M) [text/plain]
Saving to: ‘TRAIN.csv.3’

TRAIN.csv.3         100%[===================>]   7.17M  18.8MB/s    in 0.4s    

2021-05-31 20:19:41 (18.8 MB/s) - ‘TRAIN.csv.3’ saved [7524003/7524003]



In [97]:
!head TRAIN.csv

index,time_stamp,cab_provider,source,destination,distance,surge_multiplier,cab_type,fare
0,1543203646318,Lyft,Boston University,Theatre District,3.03,1.0,Lux Black XL,34.0
1,1543203646319,Uber,South Station,Theatre District,1.3,1.0,Black,18.5
2,1543203646320,Uber,Theatre District,Fenway,2.71,1.0,UberX,19.5
3,1543203646320,Lyft,Northeastern University,Beacon Hill,2.43,1.0,Lyft,10.5
4,1543203646320,Uber,Theatre District,Fenway,2.71,1.0,UberXL,32.0
5,1543203646358,Uber,Beacon Hill,North End,2.19,1.0,UberX,8.0
6,1543203646358,Uber,North Station,Fenway,3.05,1.0,WAV,10.5
7,1543203646358,Uber,Beacon Hill,North End,2.19,1.0,UberXL,13.0
8,1543203646358,Uber,Beacon Hill,North End,2.19,1.0,Black,17.5


In [98]:
import pandas as pd
import numpy as np

sources['source_Back Bay'],sources['source_Beacon Hill'],sources['source_Boston University'],
                    sources['source_Fenway'],sources['source_Financial District'],sources['source_Haymarket Square'],
                    sources['source_North End'],sources['source_North Station'],sources['source_Northeastern University'],
                    sources['source_South Station'],sources['source_Theatre District'],sources['source_West End'],
                     
                    dest['dest_Back Bay'],dest['dest_Beacon Hill'],dest['dest_Boston University'],
                    dest['dest_Fenway'],dest['dest_Financial District'],dest['dest_Haymarket Square'],
                    dest['dest_North End'],dest['dest_North Station'],dest['dest_Northeastern University'],
                    dest['dest_South Station'],dest['dest_Theatre District'],dest['dest_West End'],

                       ''' 
                    cabtype['cab_type_Black'],cabtype['cab_type_Black SUV'],cabtype['cab_type_Lux'],cabtype['cab_type_Lux Black'],
                    cabtype['cab_type_Lux Black XL'],cabtype['cab_type_Lyft'],cabtype['cab_type_Lyft XL'],cabtype['cab_type_Shared'],
                    cabtype['cab_type_UberPool'],cabtype['cab_type_UberX'],cabtype['cab_type_UberXL'],cabtype['cab_type_WAV'],
                    #dow["dow_0"],dow["dow_1"],dow["dow_2"],
                    '''   


In [99]:
def DataPipeLine(df, startup=True):
    #outlierek 
    if startup:
        df["price_per"]=df.fare/df.surge_multiplier/df.distance
        df.drop(df[df['price_per'] > 373].index, inplace = True)
        #df.drop(df[df.cab_provider=="Lyft"].index, inplace=True)
    
    df["sec"]=(df.time_stamp/1000) % (24*3600)
   
    seconds_in_day = 24*60*60
    df['sin_time'] = (np.sin(2*np.pi*df.sec/seconds_in_day))
    df['cos_time'] = (np.cos(2*np.pi*df.sec/seconds_in_day))

    sources=pd.get_dummies(df["source"],prefix='source',drop_first=False)
    dest=pd.get_dummies(df["destination"],prefix='dest',drop_first=False)
    cab=pd.get_dummies(df["cab_provider"],prefix='provider',drop_first=False)
    
    a=df.time_stamp
    df["DateTime"]=a.apply( lambda x:pd.Timestamp(x,unit="ms"))
    df["move_sum"]=df.rolling("5s",on='DateTime' ).distance.mean()
    #df["dow"]=df["DateTime"].dt.dayofweek
    
    #dow=pd.get_dummies(df["dow"],prefix='dow',drop_first=False)


    sources=pd.get_dummies(df["source"],prefix='source',drop_first=False)
    dest=pd.get_dummies(df["destination"],prefix='dest',drop_first=False)
    cab=pd.get_dummies(df["cab_provider"],prefix='provider',drop_first=False)
    cabtype=pd.get_dummies(df["cab_type"],prefix='cab_type',drop_first=False)

    new = pd.DataFrame([df.DateTime, sources.columns, dest.columns])


    Xret = pd.DataFrame([
                    
                    cab['provider_Lyft'],
                    cab['provider_Uber'],
                    sources['source_Back Bay'],sources['source_Beacon Hill'],sources['source_Boston University'],
                    sources['source_Fenway'],sources['source_Financial District'],sources['source_Haymarket Square'],
                    sources['source_North End'],sources['source_North Station'],sources['source_Northeastern University'],
                    sources['source_South Station'],sources['source_Theatre District'],sources['source_West End'],
                     
                    dest['dest_Back Bay'],dest['dest_Beacon Hill'],dest['dest_Boston University'],
                    dest['dest_Fenway'],dest['dest_Financial District'],dest['dest_Haymarket Square'],
                    dest['dest_North End'],dest['dest_North Station'],dest['dest_Northeastern University'],
                    dest['dest_South Station'],dest['dest_Theatre District'],dest['dest_West End'],

                    cabtype['cab_type_Black'],cabtype['cab_type_Black SUV'],cabtype['cab_type_Lux'],cabtype['cab_type_Lux Black'],
                    cabtype['cab_type_Lux Black XL'],cabtype['cab_type_Lyft'],cabtype['cab_type_Lyft XL'],cabtype['cab_type_Shared'],
                    cabtype['cab_type_UberPool'],cabtype['cab_type_UberX'],cabtype['cab_type_UberXL'],cabtype['cab_type_WAV'],
                    #dow["dow_0"],dow["dow_1"],dow["dow_2"],



                    df["distance"] /10,
                    df["surge_multiplier"]/3,
                    df["move_sum"]/8,
                    (df["sin_time"]/2)+0.5,
                    (df["cos_time"]/2)+0.5
                    #df.fare/df["surge_multiplier"]/df["distance"],
                    #df.fare
                    ]).transpose()
    return(Xret)



In [100]:
df=pd.read_csv("TRAIN.csv")

In [101]:
df.head()

index     time_stamp cab_provider  ... surge_multiplier      cab_type  fare
0      0  1543203646318         Lyft  ...              1.0  Lux Black XL  34.0
1      1  1543203646319         Uber  ...              1.0         Black  18.5
2      2  1543203646320         Uber  ...              1.0         UberX  19.5
3      3  1543203646320         Lyft  ...              1.0          Lyft  10.5
4      4  1543203646320         Uber  ...              1.0        UberXL  32.0

[5 rows x 9 columns]

In [102]:
X_trainn=DataPipeLine(df)   

In [103]:
df.head()

index     time_stamp  ...                DateTime  move_sum
0      0  1543203646318  ... 2018-11-26 03:40:46.318  3.030000
1      1  1543203646319  ... 2018-11-26 03:40:46.319  2.165000
2      2  1543203646320  ... 2018-11-26 03:40:46.320  2.346667
3      3  1543203646320  ... 2018-11-26 03:40:46.320  2.367500
4      4  1543203646320  ... 2018-11-26 03:40:46.320  2.436000

[5 rows x 15 columns]

In [104]:
X_trainn["surge_multiplier"].max()

1.0

In [105]:
X_trainn.move_sum.max()

0.9324999999999372

In [106]:
#df.DateTime
(df.time_stamp/1000) % (24*3600)

0        13246.318
1        13246.319
2        13246.320
3        13246.320
4        13246.320
           ...    
99995      924.049
99996      924.049
99997      924.049
99998      924.049
99999      924.049
Name: time_stamp, Length: 99970, dtype: float64

In [107]:
ytrain=df["fare"]

In [108]:
X_trainn

provider_Lyft  provider_Uber  ...  sin_time  cos_time
0                1.0            0.0  ...  0.910540  0.785407
1                0.0            1.0  ...  0.910540  0.785407
2                0.0            1.0  ...  0.910540  0.785407
3                1.0            0.0  ...  0.910540  0.785407
4                0.0            1.0  ...  0.910540  0.785407
...              ...            ...  ...       ...       ...
99995            0.0            1.0  ...  0.533574  0.998872
99996            0.0            1.0  ...  0.533574  0.998872
99997            0.0            1.0  ...  0.533574  0.998872
99998            0.0            1.0  ...  0.533574  0.998872
99999            0.0            1.0  ...  0.533574  0.998872

[99970 rows x 43 columns]

In [109]:
!rm visual_view.py
!wget https://raw.githubusercontent.com/sipocz/messer/main/visual_view.py
grafikon=None
from visual_view import grafikon
help(grafikon)

--2021-05-31 20:19:50--  https://raw.githubusercontent.com/sipocz/messer/main/visual_view.py
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1027 (1.0K) [text/plain]
Saving to: ‘visual_view.py’

visual_view.py      100%[===================>]   1.00K  --.-KB/s    in 0s      

2021-05-31 20:19:50 (43.3 MB/s) - ‘visual_view.py’ saved [1027/1027]

Help on function grafikon in module visual_view:

grafikon(fx, desc1, txt1, desc2='', txt2='', ngraf=2, c1='rgba(35,128,132,0.8)', c2='rgba(193,99,99,0.8)', title=None)
    fx: dataFrame
    desc1:column1
    txt1: label1
    desc2:column2
    txt2: label2
    ngraf: number of graph
    c1: color1
    c2: color2
    title: graph title



In [110]:
df.head()

index     time_stamp  ...                DateTime  move_sum
0      0  1543203646318  ... 2018-11-26 03:40:46.318  3.030000
1      1  1543203646319  ... 2018-11-26 03:40:46.319  2.165000
2      2  1543203646320  ... 2018-11-26 03:40:46.320  2.346667
3      3  1543203646320  ... 2018-11-26 03:40:46.320  2.367500
4      4  1543203646320  ... 2018-11-26 03:40:46.320  2.436000

[5 rows x 15 columns]

In [111]:
df.index=df.DateTime

In [112]:
df["price_per"]=df.fare/df.surge_multiplier/df.distance

In [113]:
#grafikon(X_trainn,"price_per","price_per",ngraf=1)

##szedjuk ki a 100-nál nagyobb sorokat

In [114]:
from keras.layers import InputLayer, Dense, LSTM, Input, Dropout,Embedding, Flatten
from keras.models import Sequential, Model
from keras.optimizers import SGD,Adam,Adamax,Nadam,Ftrl,Adadelta,Adagrad,Nadam
import tensorflow as tf
from tensorflow.keras.callbacks import ModelCheckpoint
from keras.backend import clear_session
from tensorflow.keras.losses import mean_absolute_percentage_error, huber,kld,mse

from keras.preprocessing.sequence import pad_sequences

In [115]:
fname="_model_1_"

In [116]:
'''
from sklearn.ensemble import IsolationForest
iso = IsolationForest(contamination=0.01)
yhat = iso.fit_predict(X_trainn)
'''

'\nfrom sklearn.ensemble import IsolationForest\niso = IsolationForest(contamination=0.01)\nyhat = iso.fit_predict(X_trainn)\n'

In [117]:
clear_session()




input_len=len(X_trainn.columns)
print(input_len)
output_size=1
drop_frac0=0.0 
drop_frac1=0.3



input1=Input(shape=(input_len,),)


#flatt=Flatten()(lstm1)

non=42

d1=Dense(input_len,activation="sigmoid")(input1)

d2=Dense(33,activation="sigmoid")(d1)

d3=Dense(13,activation="sigmoid")(d2)




pred=Dense(output_size,activation="sigmoid")(d3)

model = Model(inputs=input1, outputs=pred)

opt = tf.keras.optimizers.Adamax(learning_rate=0.001)


rmse = tf.keras.metrics.RootMeanSquaredError()
model.compile(loss="mean_squared_error",
    optimizer=opt,
    metrics=[rmse])

43


In [118]:
X_trainn

provider_Lyft  provider_Uber  ...  sin_time  cos_time
0                1.0            0.0  ...  0.910540  0.785407
1                0.0            1.0  ...  0.910540  0.785407
2                0.0            1.0  ...  0.910540  0.785407
3                1.0            0.0  ...  0.910540  0.785407
4                0.0            1.0  ...  0.910540  0.785407
...              ...            ...  ...       ...       ...
99995            0.0            1.0  ...  0.533574  0.998872
99996            0.0            1.0  ...  0.533574  0.998872
99997            0.0            1.0  ...  0.533574  0.998872
99998            0.0            1.0  ...  0.533574  0.998872
99999            0.0            1.0  ...  0.533574  0.998872

[99970 rows x 43 columns]

In [119]:
ytrain=ytrain/100

In [155]:
!rm _model*

In [183]:
def scheduler(epoch, lr):
    return 0.0001

In [184]:
callback_LR = tf.keras.callbacks.LearningRateScheduler(scheduler)

In [185]:
callbacks = [callback_LR,
       
        ModelCheckpoint(filepath=fname+"_{val_root_mean_squared_error:.5f}__.hdf5", monitor='val_root_mean_squared_error',
                        verbose=2, save_best_only=True, mode='min')]

In [ ]:
history = model.fit( X_trainn,ytrain, 
                        epochs=555, 
                        batch_size=10,validation_split=0.3,
                        verbose=1,
                        callbacks=callbacks,
                              
                              )

Epoch 1/555
6998/6998 [==============================] - 11s 2ms/step - loss: 3.7972e-04 - root_mean_squared_error: 0.0196 - val_loss: 3.8532e-04 - val_root_mean_squared_error: 0.0196

Epoch 00001: val_root_mean_squared_error improved from inf to 0.01964, saving model to _model_1__0.01964__.hdf5
Epoch 2/555
6998/6998 [==============================] - 11s 2ms/step - loss: 3.7948e-04 - root_mean_squared_error: 0.0191 - val_loss: 3.8454e-04 - val_root_mean_squared_error: 0.0196

Epoch 00002: val_root_mean_squared_error improved from 0.01964 to 0.01961, saving model to _model_1__0.01961__.hdf5
Epoch 3/555
6998/6998 [==============================] - 11s 2ms/step - loss: 3.7927e-04 - root_mean_squared_error: 0.0195 - val_loss: 3.8438e-04 - val_root_mean_squared_error: 0.0196

Epoch 00003: val_root_mean_squared_error improved from 0.01961 to 0.01961, saving model to _model_1__0.01961__.hdf5
Epoch 4/555
6998/6998 [==============================] - 12s 2ms/step - loss: 3.7899e-04 - root_mean_

In [ ]:
#!rm _model*

In [157]:
datag=pd.DataFrame()
y_pred=model.predict(X_trainn)



In [158]:
datag["pred"]=list(y_pred.T[0])
datag["y"]=list(y_pred)
datag["delta"]=y_pred.T[0]-ytrain

In [159]:
grafikon(datag,"pred","pred","delta","delta")

## betöltés

In [ ]:
!pip install xgboost

In [ ]:
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.datasets import make_regression
from sklearn.neural_network import MLPRegressor

#regr = GradientBoostingRegressor(n_estimators=100,max_depth=500, random_state=0)
#regr.fit(X_trainn, ytrain)

regr = MLPRegressor(random_state=1, max_iter=500,verbose=True,tol=1e-8)
regr.fit(X_trainn, ytrain)



In [ ]:
import xgboost as xgb
xgbr = xgb.XGBRegressor(n_estimators=300,   verbosity=2, max_depth=40) 
#print(xgbr)
xgbr.fit(X_trainn, ytrain,)

In [ ]:
score = xgbr.score(X_trainn, ytrain,)  
print("Training score: ", score)


In [160]:
modelname="_model_1__0.01983__.hdf5"

In [ ]:
!wget https://github.com/sipocz/CabPrice/raw/main/_model_1__1.64576__.hdf5

In [161]:
!wget https://github.com/sipocz/CabPrice/raw/B20210507/TEST.csv

--2021-05-31 20:53:35--  https://github.com/sipocz/CabPrice/raw/B20210507/TEST.csv
Resolving github.com (github.com)... 140.82.112.3
Connecting to github.com (github.com)|140.82.112.3|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://raw.githubusercontent.com/sipocz/CabPrice/B20210507/TEST.csv [following]
--2021-05-31 20:53:35--  https://raw.githubusercontent.com/sipocz/CabPrice/B20210507/TEST.csv
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.111.133, 185.199.110.133, 185.199.108.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.111.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1757163 (1.7M) [text/plain]
Saving to: ‘TEST.csv.1’

TEST.csv.1          100%[===================>]   1.67M  --.-KB/s    in 0.1s    

2021-05-31 20:53:36 (16.2 MB/s) - ‘TEST.csv.1’ saved [1757163/1757163]



In [162]:


model=tf.keras.models.load_model(modelname)

In [163]:
dft=pd.read_csv("TEST.csv")

In [164]:
dft.head()

index     time_stamp cab_provider  ... distance surge_multiplier      cab_type
0      0  1543364124206         Lyft  ...     0.59              1.0           Lux
1      1  1543364124206         Lyft  ...     0.59              1.0  Lux Black XL
2      2  1543364124206         Uber  ...     6.83              1.0         UberX
3      3  1543364124206         Uber  ...     1.35              1.0        UberXL
4      4  1543364124206         Lyft  ...     0.59              1.0       Lyft XL

[5 rows x 8 columns]

In [165]:
dft.tail()

index     time_stamp cab_provider  ... distance surge_multiplier   cab_type
24995  24995  1543413683462         Uber  ...     3.05              1.0   UberPool
24996  24996  1543413683462         Uber  ...     3.05              1.0        WAV
24997  24997  1543413683462         Uber  ...     3.05              1.0  Black SUV
24998  24998  1543413683687         Lyft  ...     2.96              1.0     Shared
24999  24999  1543413683687         Lyft  ...     2.96              1.0        Lux

[5 rows x 8 columns]

In [166]:

X_test=DataPipeLine(dft,startup=False)

In [167]:
X_test.head()

provider_Lyft  provider_Uber  source_Back Bay  ...  move_sum  sin_time  cos_time
0            1.0            0.0              0.0  ...   0.07375   0.53358  0.998871
1            1.0            0.0              0.0  ...   0.07375   0.53358  0.998871
2            0.0            1.0              0.0  ...   0.33375   0.53358  0.998871
3            0.0            1.0              0.0  ...   0.29250   0.53358  0.998871
4            1.0            0.0              0.0  ...   0.24875   0.53358  0.998871

[5 rows x 43 columns]

In [168]:
y_test=model.predict(X_test)


In [169]:
y_regr = y_test*100

In [170]:
y_regr

array([[12.680596 ],
       [24.0378   ],
       [19.374636 ],
       ...,
       [33.50538  ],
       [ 6.6094785],
       [19.449753 ]], dtype=float32)

In [171]:
y_regr

array([[12.680596 ],
       [24.0378   ],
       [19.374636 ],
       ...,
       [33.50538  ],
       [ 6.6094785],
       [19.449753 ]], dtype=float32)

In [172]:
odf=pd.DataFrame(y_regr)

In [173]:
odf.head()

0
0  12.680596
1  24.037800
2  19.374636
3  13.126999
4  11.024490

In [146]:
!wget https://github.com/sipocz/CabPrice/raw/B20210507/sample_submission.csv

--2021-05-31 20:34:12--  https://github.com/sipocz/CabPrice/raw/B20210507/sample_submission.csv
Resolving github.com (github.com)... 140.82.113.4
Connecting to github.com (github.com)|140.82.113.4|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://raw.githubusercontent.com/sipocz/CabPrice/B20210507/sample_submission.csv [following]
--2021-05-31 20:34:12--  https://raw.githubusercontent.com/sipocz/CabPrice/B20210507/sample_submission.csv
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.109.133, 185.199.108.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.109.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 106 [text/plain]
Saving to: ‘sample_submission.csv’

sample_submission.c 100%[===================>]     106  --.-KB/s    in 0s      

2021-05-31 20:34:12 (4.24 MB/s) - ‘sample_submission.csv’ saved [106/106]



In [147]:
!head sample_submission.csv

index,fare
0,11.0
1,26.0
2,18.5
3,11.5
4,9.0
5,10.5
6,7.0
7,7.0
8,26.0


In [148]:
def round_half(a):
    return(a)
    import math
    e=math.floor(a)
    m=a-e
    if m>0.75:
        return e+1
    if m<0.25:
        return e
    return e+0.5

In [174]:
odf.columns=["fare2"]
odf.index.name="index"
odf["fare"]=odf["fare2"].apply(lambda x:round_half(x))


In [175]:
del odf["fare2"] #drop(['algebra', 'chemistry'], axis=1)
odf.head()

fare
index           
0      12.680596
1      24.037800
2      19.374636
3      13.126999
4      11.024490

In [176]:
odf.to_csv("submission_32.csv")

In [177]:
! head submission_32.csv

index,fare
0,12.680596351623535
1,24.037799835205078
2,19.374635696411133
3,13.126998901367188
4,11.024490356445312
5,9.92293930053711
6,5.778959274291992
7,6.9289116859436035
8,28.675151824951172
